In [1]:
%load_ext Cython

In [10]:
%%cython
import numpy as np
import pandas as pd
#dictionary型に変換する関数
def two_list_to_dict(key_list, val_list):
      return dict(zip(key_list, val_list))

#csvを読み込んで行ごとに分割
def read_file(filename):
    with open(str(filename),'r',encoding='utf8') as fbrand:
        txt=fbrand.read() 
        lines = txt.split("\n")
        return lines

#csvの各行を分割してコーデごとのブランドlistのlistを作る.
def make_Coordinate(lines):
    Coordinate=[]
    #重複のない辞書にするためにsetを用いる
    s=set()
    for line in lines:
        brands=line.split(",")
        Coordinate.append(brands)
    return Coordinate

#good_tagsのみに絞る
def make_goodtags(lines,good_tags_set):
    good_tags_list=[]
    #重複のない辞書にするためにsetを用いる
    s=set()
    s=good_tags_set
    for line in lines:
        tags=line.split(",")
        good_tags=[t for t in tags if t in s] 
        #if len(good_tags) == 0:
        good_tags_list.append(good_tags)
    return good_tags_list

def make_brandset(lines):
    #重複のない辞書にするためにsetを用いる
        s=set()
        for line in lines:
            brands=line.split(",")
            for brand in brands:
                s.add(brand)
        brand_set=list(s)
        print(len(brand_set))
        return brand_set

def make_dict(brandset):
    #dictionaryのindex
    index=[]
    for i in range(len(brandset)):
        index.append(i)
    #辞書
    brand_dict=two_list_to_dict(brandset,index)
    return brand_dict

def brand_to_dictnum(Coordinates,brand_dict):
    W = [] # words
    #ブランドと補助情報の文書ごとのリストを作る
    for Coordinate in Coordinates:
    #list()をつけない場合iterator objectが帰ってくる
        W.append(list(map(lambda v:brand_dict[v],Coordinate)))
    return W

#結果に関する関数  
def brand_to_topic(Coordinates,nctm_Z): #nctm.Zはnctm.fitの結果が入っている
    brand_topic=[]
    for brands, Topics in zip(Coordinates,nctm_Z):
        for brand,Topic in zip(brands,Topics):
            pair=[brand,Topic]
            brand_topic.append(pair)
    return brand_topic

def brand_topic_list_f(brand_topic,K):
    brand_topic_list=[]
    for i in range(K):
        aaa=[x for x in brand_topic if x[1] == i]
        #print(aaa)
        brand_topic_list.append(aaa)
    return brand_topic_list

def t_setlist_brand_f(brand_topic_list,K):
    #brandについて
    t_setlist_brand=[] #各トピックごとのbrandのsetを代入するリスト
    for i in range(K): #各トピックで回す
        a=[] #各トピックでsetを作るためのローカル変数
        for item in brand_topic_list[i]:
            a.append(item[0])
        a=set(a) #セットにする
        a=list(a) #リストに直す
        t_setlist_brand.append(a) #現在のトピックのsetをグローバルのリストに追加
    #print(t_setlist[0]) 
    return t_setlist_brand

def count_topic_f(brand_topic_list,t_setlist_brand,K):
    count_topic=[] #全トピックの出現回数リストのリスト
    for i in range(K): #トピックループ
        count=np.zeros((len(t_setlist_brand[i]))) #今見ているトピックのsetの長さ分のbrandカウント配列を初期化
        for item in brand_topic_list[i]: #itemはリスト
            count[t_setlist_brand[i].index(item[0])]+=1 #今見ているbrandのインデックスをカウントアップ
        count_topic.append(count) #一つのトピックについて見終えたらグローバルに追加
    return count_topic

def count_noise(tag_set,R):
    count=np.zeros(len(tag_set)) #今見ているトピックのsetの長さ分のbrandカウント配列を初期化
    for item in R: #itemはリスト
        count[item]+=1 #今見ているbrandのインデックスをカウントアップ
    return count

def write_result(filename,t_setlist_brand,count_topic):
    topic_num=0
    for item,count in zip(t_setlist_brand,count_topic):
        tuples=[]
        for b,c in zip(item,count):
            tuples.append(tuple((b,c)))
        tuples.sort(key=lambda x:x[1],reverse=True) #x[1]に出現回数が入っているので多い順にソート
        df=pd.DataFrame(tuples)
        if topic_num < 10:
            df.to_csv( './cleansing_data/result_iter10000/topic75/pattern001/topic'+'0'+str(topic_num)+str(filename), index=False )
        else:
            df.to_csv( './cleansing_data/result_iter10000/topic75/pattern001/topic'+str(topic_num)+str(filename), index=False )
        topic_num+=1
    print("END")

def outputR(filename,nctmR):
    import csv
    with open('./cleansing_data/result_iter10000/topic75/pattern001/'+str(filename),'w') as f:
        writer = csv.writer(f, lineterminator='\n')
        writer.writerows(nctmR)

In [3]:
good_tag_lines=read_file('./cleansing_data/goodtags10000.csv')
#good_tag_input=make_Coordinate(good_tag_lines)
good_tag_input=make_Coordinate(good_tag_lines)
Coordinate_lines=read_file('./cleansing_data/goodCoords10000.csv')
# good_Coordinate_input=make_Coordinate(Coordinate_lines)
good_Coordinate_input=make_Coordinate(Coordinate_lines)

In [4]:
# import csv #書き込み時にコメントアウト外す
# with open('./cleansing_data/goodCoords10000.csv','w') as fC:
#     writer = csv.writer(fC, lineterminator='\n')
#     writer.writerows(good_Coordinate_input)
# with open('./cleansing_data/goodtags10000.csv','w') as ft:
#     writer = csv.writer(ft, lineterminator='\n')
#     writer.writerows(good_tag_input)

In [5]:
# モデルに入れる前に形式を合わせる必要がある
tag_set=make_brandset(good_tag_lines)
# tag_set=make_brandset(good_tag_lines)
tag_dict=make_dict(tag_set)
brand_set=make_brandset(Coordinate_lines)
# brand_set=make_brandset(Coordinate_lines)
brand_dict=make_dict(brand_set)
tag_W=brand_to_dictnum(good_tag_input,tag_dict)
Coordinate_W=brand_to_dictnum(good_Coordinate_input,brand_dict)

3219
3298


In [6]:
print(good_tag_input[0:10])
print(tag_W[0:10])

[["who's who chico", 'シンプル', 'フレアスカート', 'ニットスカート'], ['シンプル', 'スニーカー', 'タートルネックニット', 'ロシアン帽', '青文字系', 'ニコアンド', 'コンバース', '冬'], ['WEGO', '出勤コーデ', 'ヘアバンド', 'お団子ヘアー', 'レーストップス', 'カーディガン', 'リボン', 'コンバース', 'GU'], ['冬', 'ワンピース', '白ニット', 'ダッフルコート', 'ミニスカート', 'ヘアバンド'], ['結婚式', 'パーティースタイル', 'オケージョン', 'オールインワン', 'サロペット', 'ダウンジャケット', 'ネックレス', 'きれいめカジュアル'], ['きれいめカジュアル', 'カジュアル', 'ホワイト', 'ベージュ', 'カットオフ', 'キャップ', 'ストリート', 'スウェット', 'ローキャップ', 'ラフ'], ['アウター', 'ピンク', 'ノーカラーコート', 'シャギー', 'ワイドスリーブ', 'コーデュロイ', 'ニット'], ['ダメージデニムパンツ', 'レオパード', 'ショートブーツ', 'Doシンプル部', 'いい友連合', 'ロングカーディガン', 'オトナカジュアル', 'きれいめカジュアル', 'お団子ヘアー', 'ダメージデニム'], ['ミリタリー', 'ミリタリージャケット', 'フライトジャケット', '黒スキニー', 'ユニクロ', 'ドレスシューズ', '白ソックス', '冬'], ['シンプル', 'ダル着', 'チャンピオン', 'AVIREX', 'ディッキーズ(Dickies)', 'ちょっとそこまで']]
[[449, 1213, 2150, 3102], [1213, 524, 560, 296, 43, 1797, 1192, 872], [2237, 2483, 45, 2327, 2469, 1367, 2497, 1192, 1000], [872, 2818, 290, 2437, 53, 45], [2106, 3154, 253, 1550, 284, 2049, 3, 78], [78, 874, 2355, 398, 1791, 609, 1998

## ハイパーパラメータをいじるのがよさそう
どうやらRがほとんど0に収束してしまうのはこれが原因ぽい

In [7]:
from nctm import NCTM
W=Coordinate_W
X=tag_W
Vw = len(W)
Vx = len(X)
K = 75
alpha = 0.01
beta= 0.01
gamma= 0.01
eta = 1.0
max_iter = 10000
nctm = NCTM(K=K, alpha=alpha, beta=beta, gamma=gamma, eta=eta, max_iter=max_iter)

In [8]:
import time
start = time.time()
nctm.fit(W,X,Vw,Vx)
elapsed_time = time.time() - start
print("elapsed_time:{0}".format(elapsed_time))

The installed widget Javascript is the wrong version.


[array([0, 1, 0, 0]), array([0, 1, 0, 1, 1, 0, 1, 0]), array([1, 0, 1, 1, 0, 0, 1, 0, 0]), array([1, 1, 0, 0, 1, 1]), array([1, 1, 0, 0, 1, 1, 0, 0]), array([1, 0, 1, 0, 1, 1, 1, 0, 1, 1]), array([1, 1, 1, 0, 1, 0, 1]), array([0, 0, 1, 0, 0, 0, 1, 0, 0, 0]), array([0, 1, 1, 1, 0, 1, 1, 1]), array([0, 0, 1, 0, 0, 1])]
[array([1, 1, 0, 0]), array([0, 1, 0, 0, 0, 0, 1, 0]), array([0, 0, 1, 1, 1, 1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1]), array([0, 0, 1, 1, 0, 0, 0, 1]), array([1, 1, 0, 0, 0, 0, 1, 0, 1, 1]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 0, 0, 0, 0, 1, 0, 0]), array([1, 1, 0, 1, 0, 1, 1, 0]), array([0, 1, 1, 0, 0, 0])]
[array([0, 0, 0, 0]), array([1, 1, 0, 1, 0, 0, 0, 0]), array([0, 0, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 1]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([1, 0, 1, 0, 0, 1, 1, 0, 0, 1]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 1, 0, 0]), array([1, 1, 1, 0, 0, 0])]
[array([0, 1, 0, 0]), array([0, 0, 0, 0, 0,

[array([0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 0, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 1, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 0, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 1,

[array([0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([0, 0, 0, 0]), array([0, 0, 0, 0, 0,

[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 1, 0, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1,

...

[array([1, 0, 0, 1]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 1, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([1, 1, 0, 1, 1, 0, 0, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 1, 1, 0, 0]), array([0, 0, 1, 1, 1, 0, 0, 0, 0, 0]), array([1, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([1, 1, 0, 1, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1,

[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 1, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 1]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1,

[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 1, 1, 1, 0, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 1, 1,

[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 1, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 0, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 0, 0, 0, 0]), array([0, 1, 0, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 1, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 1, 0, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1,

[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 1]), array([0, 0, 0, 0, 1, 1, 0, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 1, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 1, 1, 0, 0]), array([0, 1, 1, 1, 1, 1])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1, 1, 1, 0]), array([1, 1, 0, 0, 1, 0, 1, 0, 1]), array([0, 0, 0, 0, 0, 0]), array([1, 1, 1, 0, 0, 0, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 1, 0]), array([0, 0, 0, 0, 1, 0, 0]), array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]), array([0, 0, 0, 1, 1, 1, 0, 0]), array([0, 1, 1, 1, 1, 0])]
[array([1, 0, 0, 0]), array([0, 0, 0, 0, 1,

In [11]:
brand_topic=brand_to_topic(good_Coordinate_input,nctm.Z)
tag_topic=brand_to_topic(good_tag_input,nctm.Y)

#topicごとにブランドとトピックの組をまとめる
brand_topic_list=brand_topic_list_f(brand_topic,K)
tag_topic_list=brand_topic_list_f(tag_topic,K)

#トピックごとに出現ブランドのセットを作る
t_setlist_brand=t_setlist_brand_f(brand_topic_list,K)
t_setlist_tag=t_setlist_brand_f(tag_topic_list,K)

# 各トピックごとのサイズの確認
TopicBrandSize=[]
TopicTagSize=[]
index=[]
for i in range(len(t_setlist_brand)):
    TopicBrandSize.append(len(t_setlist_brand[i]))
    TopicTagSize.append(len(t_setlist_tag[i]))
    index.append(i)
print(TopicBrandSize)
print(TopicTagSize)

[70, 52, 66, 77, 47, 64, 80, 110, 104, 75, 81, 28, 75, 69, 100, 94, 43, 87, 102, 110, 81, 90, 81, 71, 56, 73, 77, 83, 113, 143, 62, 69, 118, 66, 96, 73, 105, 94, 70, 67, 81, 71, 64, 91, 52, 53, 83, 59, 63, 89, 96, 81, 64, 92, 74, 41, 62, 109, 85, 105, 84, 64, 58, 57, 68, 58, 84, 69, 68, 65, 87, 77, 58, 184, 115]
[242, 198, 237, 181, 269, 228, 221, 368, 278, 266, 297, 167, 223, 194, 230, 390, 175, 310, 326, 243, 191, 319, 303, 222, 238, 372, 274, 256, 250, 394, 208, 261, 252, 224, 254, 212, 241, 325, 276, 166, 233, 207, 271, 269, 157, 309, 359, 258, 238, 230, 254, 348, 197, 306, 199, 172, 300, 306, 269, 267, 353, 258, 223, 286, 188, 189, 246, 200, 197, 193, 230, 272, 229, 304, 274]


In [46]:
#0になっているタグを除去しないといけない．0になっているタグもトピックに分配されてしまっている
# print(nctm.R[0:100])

In [12]:
#セットを用いて出現回数をカウント
count_topic_brand=count_topic_f(brand_topic_list,t_setlist_brand,K)
count_topic_tag=count_topic_f(tag_topic_list,t_setlist_tag,K)

In [13]:
#結果の書き込み
import pandas as pd
write_result('brands.csv',t_setlist_brand,count_topic_brand)
write_result('tags.csv',t_setlist_tag,count_topic_tag)

END
END


In [14]:
# ノイズ配列の保存
import csv
outputR('nctmR.csv',nctm.R)

In [14]:
## ノイズと判断されたものについて
noise_list=[]
for r,tag in zip(nctm.R,X):
    for r0, tag0 in zip(r,tag) :
        print(r0,tag0)
        if(r0==0):
            noise_list.append(tag0)

1 562
0 966
0 687
0 2457
0 966
0 394
0 990
0 86
1 2969
1 3216
0 2875
0 928
1 3038
1 2539
0 1050
0 1409
0 2932
0 491
0 2633
0 2875
0 373
0 928
0 526
0 1986
0 2377
0 2900
0 1050
1 23
0 2874
1 244
0 2179
0 2515
0 2507
0 2142
0 736
0 736
0 1941
0 2552
0 456
0 3043
0 2849
0 1578
0 1764
1 2742
0 1635
0 1044
0 2821
0 1284
1 357
1 150
0 1769
0 1314
0 401
0 2259
0 138
0 2145
0 827
0 2294
0 1368
0 736
0 1409
0 2965
0 872
0 1770
0 2014
0 2747
0 651
0 1394
0 2339
0 928
0 966
0 958
1 2676
1 301
1 2164
0 724
0 966
0 1398
0 2417
0 1314
0 1644
0 367
1 1408
0 406
0 1052
1 1065
0 736
1 2153
0 373
1 1977
1 1677
0 494
0 966
1 188
0 928
0 736
0 871
1 2747
0 1941
0 564
1 225
0 1660
1 2352
0 197
1 1848
1 509
0 966
0 1281
0 2008
0 1202
1 1352
0 928
0 736
0 1725
1 1301
0 730
0 401
0 507
0 966
1 424
0 659
1 1188
0 2377
1 1302
0 928
0 736
0 871
0 925
1 3195
0 1619
0 1820
1 2698
1 2610
1 2176
0 373
0 709
0 1201
0 769
0 2190
0 1890
0 966
0 2876
0 966
0 394
0 1281
0 3108
0 1398
0 2507
0 3191
0 495
0 1789
0 928
0 33

0 2779
1 2722
1 1598
1 1921
0 1068
0 966
0 990
0 456
0 2417
0 2721
1 9
0 1625
1 371
0 143
0 2015
1 1037
1 474
0 1635
0 143
0 1451
0 1314
0 1578
0 394
0 2875
0 373
0 1725
0 2058
0 2123
0 928
0 871
0 1451
0 1563
0 2366
1 1459
0 1644
1 288
1 145
1 1346
0 1789
0 1987
1 2708
1 225
1 111
1 1625
0 928
0 736
0 1635
0 871
0 1368
0 1619
0 3117
0 2721
0 2507
0 1677
0 889
0 494
0 15
0 1384
1 1634
1 1233
0 2507
0 966
0 40
0 871
0 2876
0 928
0 1724
1 1773
1 2708
0 1007
0 966
0 394
0 928
1 617
0 1301
1 3132
0 928
0 330
0 3028
1 474
0 1368
0 2082
0 2789
0 2058
0 394
0 966
0 1398
0 928
0 2417
0 373
0 3165
0 377
0 1451
0 2230
0 1635
1 2119
1 455
0 564
1 1020
0 1764
0 2109
1 1990
0 1574
0 966
0 149
1 1810
0 928
0 1398
0 3044
0 2058
0 394
1 301
0 1941
0 2797
0 1281
0 928
0 929
0 149
0 143
1 2319
0 197
1 474
1 2373
0 1295
1 3038
0 394
0 367
0 564
0 2876
0 736
0 1753
0 2109
0 330
0 2709
1 2169
1 2499
1 2168
0 2747
1 1980
0 1370
0 736
0 1368
0 928
1 2958
0 2803
0 651
1 2708
0 1314
0 2639
1 1137
1 2701
1 1215

1 713
0 2922
1 3100
1 821
0 1644
1 198
1 1325
1 2529
1 1030
0 197
0 1644
1 3104
0 3023
1 2735
1 2807
0 2626
1 2195
1 1076
1 2529
0 928
0 736
0 1941
0 1368
0 651
0 401
0 382
0 1280
0 2789
0 2875
0 1848
0 1725
1 1821
1 162
0 1941
0 871
0 1879
0 1281
0 2259
1 1280
0 2849
0 2365
0 2321
1 1422
0 1848
0 1725
1 1821
1 162
0 1753
0 1236
0 2253
0 1644
0 2109
0 2876
1 1046
0 1677
0 494
1 738
1 67
0 928
1 2584
0 3052
0 1893
0 1941
1 1656
0 928
1 785
0 86
1 374
1 215
0 1987
1 2052
0 1644
1 828
0 928
0 871
1 2747
0 651
0 1986
1 2525
0 956
0 504
0 928
0 736
0 1941
0 871
0 1202
0 143
1 3038
1 1821
1 162
0 1834
1 2445
1 1821
1 162
0 928
0 2853
0 2254
0 406
0 1181
0 111
0 253
0 1644
0 2365
0 1052
1 1325
1 2785
1 1644
1 2224
0 1987
0 928
1 1578
1 1370
1 2755
0 2379
0 2789
0 1451
0 1314
0 401
0 1941
0 507
0 871
0 1202
0 1281
0 2789
0 2812
1 480
0 2754
0 928
0 928
0 966
0 367
0 1368
0 651
0 2469
0 871
0 1451
0 928
1 922
0 697
0 504
0 687
0 367
1 1550
0 564
0 1384
0 457
1 665
0 1603
0 1368
0 2797
0 149
0 5

1 1132
0 1174
0 172
0 2803
0 2058
0 1764
0 2367
0 1314
1 2856
1 2777
0 143
0 394
0 2849
1 944
0 871
0 2876
0 966
1 3096
0 1202
0 1301
0 928
0 2109
0 907
0 1008
0 2898
0 1941
1 1755
0 966
0 1383
1 872
1 1422
1 292
1 1552
1 3204
1 1132
0 495
0 1314
0 2721
0 2755
1 1215
0 112
0 966
0 2552
0 2876
1 1137
1 3204
0 276
0 1879
0 3108
0 615
0 1677
0 1501
1 1163
0 928
0 1941
0 1368
0 615
1 1820
0 3028
0 901
0 197
0 2751
0 928
0 1941
0 1202
1 1439
0 1298
0 1619
0 394
0 736
1 923
0 2283
0 1753
0 526
1 1887
1 1109
0 2874
1 1453
1 2524
1 1672
1 2887
0 1236
0 928
0 1941
0 394
0 1281
0 1202
0 1368
0 1407
0 1301
0 928
1 1194
1 2087
1 518
1 2500
1 2229
1 1571
1 2354
1 2366
0 928
1 860
0 928
0 1368
0 1941
0 1314
0 1677
0 2749
0 373
1 3038
0 1947
1 2469
0 1644
0 1036
1 1742
0 1937
1 3217
0 1941
0 1398
0 1619
0 495
0 1993
0 474
0 2720
0 526
0 705
0 2058
0 1949
1 1873
0 367
0 1416
0 841
0 1941
0 394
0 1603
0 1451
0 928
0 1941
0 3108
0 651
0 1451
0 2319
0 126
1 1994
0 564
0 526
0 1113
0 2633
1 1887
1 1109
1 

0 1368
0 394
1 2308
0 1174
0 246
1 1647
0 1202
0 1578
0 872
0 811
0 1941
0 928
0 394
0 377
0 1368
0 2253
1 41
0 2797
0 850
1 1818
0 1036
0 1082
0 2417
1 1215
1 710
0 928
0 1941
0 1764
0 1281
0 1574
0 394
1 1725
1 1708
0 1834
1 1215
0 1482
1 67
0 1045
0 2109
0 615
0 2875
0 2072
0 1584
0 143
1 1242
1 1873
0 1725
0 928
0 871
0 1603
1 1711
0 1895
0 1769
1 576
0 615
1 2556
1 803
0 1438
0 1309
1 2806
1 2874
1 23
0 1774
0 1366
0 1789
1 1865
0 2797
0 1368
0 1941
0 3108
0 1036
1 1287
0 143
0 626
0 978
1 1856
0 928
0 1368
0 966
0 2008
0 1314
0 2751
0 1438
0 1774
1 1793
1 572
1 1954
1 903
0 1319
0 1314
0 1941
0 2552
0 3108
1 1766
0 1789
1 3031
1 2331
0 1398
1 1636
0 3052
0 3108
0 1315
0 1758
0 1577
0 2721
1 73
0 1368
1 2476
1 1555
1 373
0 3165
0 2821
0 233
0 394
0 1603
0 1281
0 1711
1 2123
0 1619
0 2321
0 3110
0 495
0 507
0 929
0 526
1 1055
0 1201
0 357
0 928
0 1941
0 394
0 401
0 990
0 1368
0 1941
1 3062
0 2515
0 491
0 1281
0 1941
0 966
0 149
0 400
1 1672
1 2887
0 1368
0 1304
0 2876
0 925
0 1366


...

0 1774
1 2812
0 394
0 1281
0 1677
0 2876
0 1753
0 1398
0 1036
0 1368
1 2469
0 929
1 2499
1 1253
1 1994
1 497
0 2768
1 2035
0 1941
0 2976
0 2554
0 1314
0 2230
0 615
1 2895
0 1953
0 2554
0 2321
0 1366
0 1635
0 1753
0 925
0 709
1 1181
0 1281
0 2876
0 1753
1 2117
1 2072
0 1398
1 1036
0 1368
1 2469
0 615
1 1702
1 1491
0 2912
1 3204
1 738
0 149
0 3052
0 1753
0 3108
0 1635
0 2294
0 1758
0 2876
0 3165
0 495
0 1281
0 164
0 2789
0 907
0 2875
0 336
0 1036
0 651
0 1711
0 2104
0 2321
0 1335
0 172
0 1687
0 1334
1 3150
1 1740
1 1882
0 966
1 1223
0 2876
0 1199
0 651
0 1574
0 1314
0 2875
0 928
0 172
1 1708
0 1314
0 2321
0 1941
1 615
0 2633
0 2340
0 925
0 1619
0 572
1 1872
0 1368
0 2554
0 1941
0 138
0 2876
1 2566
1 1087
1 2273
1 796
1 666
0 1571
0 526
0 1941
0 1393
0 978
0 928
0 826
1 1872
0 1774
1 2816
0 2639
1 2486
0 1941
0 564
0 2321
0 1366
0 2554
0 925
0 1619
1 2545
1 437
0 406
0 1413
0 2554
0 925
0 709
0 1314
0 382
0 1113
0 1436
1 647
0 1366
0 1987
1 2455
1 531
0 1753
0 1174
0 2925
0 2554
0 2321
0 

1 2105
1 1550
0 1724
0 1398
1 1137
0 1619
0 1281
0 1451
0 2321
0 1687
0 1201
0 2797
0 2554
0 2321
0 1366
0 1753
0 1774
0 1113
0 925
0 2294
0 1662
0 2554
1 1236
0 1181
1 2175
1 1675
0 2812
0 394
0 3165
0 1574
0 2789
0 1654
0 1578
0 2876
0 1774
0 143
0 2602
0 2109
0 126
0 2755
1 9
0 2321
0 1635
0 2321
0 1314
0 2789
0 1619
0 1281
1 2645
0 253
0 2876
0 1753
0 2507
0 1314
0 925
0 2190
0 1986
1 2506
0 1644
0 1036
1 3104
1 1989
1 1212
0 2554
0 2321
0 1366
0 1635
0 1789
0 1774
0 925
0 1314
0 2844
0 1617
1 281
0 1181
0 526
0 40
0 1644
1 2503
0 2554
1 1969
1 1794
1 2766
0 147
0 1789
0 1764
0 2602
1 2239
0 2470
0 1774
0 1359
1 2148
1 1215
0 1137
0 1266
1 881
1 466
1 1482
0 2554
0 1773
0 966
0 925
0 2925
0 256
0 929
1 197
0 2876
0 1004
0 2747
0 2554
0 2321
0 1366
0 1953
0 1789
0 394
0 1281
1 1396
0 2554
0 1838
0 2554
0 2321
0 1366
0 1789
0 925
0 1769
0 1646
0 2638
0 406
0 2145
0 1368
0 928
0 1635
0 2311
0 2417
0 1486
0 966
0 1644
0 3023
0 1482
0 1635
0 1789
0 3013
0 1619
0 1279
0 394
0 253
0 2501


0 462
0 2876
1 2079
0 494
0 2876
0 3165
0 1774
0 2507
0 1201
0 1281
0 871
0 1368
0 1724
0 966
1 742
0 1202
0 2789
0 925
0 2365
0 1176
0 401
0 1789
0 2321
0 1789
0 1753
0 709
0 990
0 2515
0 1806
0 783
0 1451
0 2876
0 3165
0 651
0 1578
0 925
0 564
0 1619
0 2709
0 1309
0 830
0 2876
0 1654
0 1774
0 1578
0 373
0 2554
1 2584
1 54
1 2701
0 1137
1 1215
1 2046
1 2763
1 3048
0 1941
1 438
0 2321
0 1733
0 2554
0 2321
0 1789
0 1753
1 1301
0 615
0 1398
0 2109
0 330
0 1569
0 373
0 2876
0 1941
0 2721
0 1807
0 394
0 164
0 1724
0 1368
0 2539
0 1099
0 651
1 2739
0 903
0 960
0 1366
0 709
0 1753
1 1345
0 3159
1 2050
0 2876
0 651
0 1199
0 1578
0 674
0 1870
0 2705
0 2721
0 2791
1 1778
1 2607
0 2554
0 1753
0 1366
1 764
0 2925
0 1626
0 1662
1 830
0 1201
0 1202
0 373
0 491
0 2294
1 1983
0 2602
1 816
0 1834
0 1654
0 2554
0 2321
0 1635
0 1789
0 1753
0 1366
0 1774
0 53
0 2797
1 57
0 2321
0 1635
0 1789
0 1753
0 1366
0 1398
0 2554
0 1753
0 1774
0 526
0 929
1 1840
1 2599
1 439
1 2395
0 2789
0 1770
0 2058
1 292
1 469


0 1398
0 1789
1 433
1 1033
0 2875
0 1603
0 2321
0 2554
0 1366
0 1789
0 1398
0 2821
0 1584
0 1569
0 2321
0 1398
0 1635
0 1789
0 928
0 2638
0 494
0 2876
0 3165
0 373
0 1753
0 1201
0 1774
1 2354
0 2501
0 2339
1 197
0 2554
1 2518
0 1133
0 709
0 2008
1 2044
0 2321
0 2789
0 373
0 1789
0 373
0 2554
0 1398
0 2153
0 2058
1 2176
0 53
0 709
1 721
1 373
1 3106
1 22
1 1580
0 494
1 1042
0 497
1 1406
1 1316
0 1848
0 1133
0 1999
0 925
0 3165
0 111
0 1619
0 615
0 491
1 1055
1 2875
0 2751
1 950
0 1879
0 1789
0 1398
0 2705
0 2058
0 504
1 460
0 30
0 2142
0 564
0 2365
0 1314
0 3108
0 576
0 736
0 2554
0 2321
0 1635
0 1753
0 1366
0 1398
0 1314
0 2417
0 281
1 1797
0 2554
0 2321
0 1789
1 433
1 3074
0 1314
0 111
1 504
0 373
1 22
0 2789
0 2230
0 1977
0 2092
0 739
0 2720
1 2512
0 1578
0 2319
0 1635
0 1789
0 1753
0 2554
0 2321
0 1753
0 1398
0 709
0 281
0 615
0 1660
0 1036
1 428
0 2789
0 699
0 406
0 2875
0 1652
0 2554
0 1088
0 2721
0 185
0 1314
0 1724
0 966
0 138
0 1724
1 881
0 2554
0 1398
1 1579
0 504
0 68
1 710
1

KeyboardInterrupt: 

In [16]:
print(len(set(noise_list)))

3144


In [24]:
count=0
for n in noise_list:
    if n==3477:
        count+=1
print(count)

608


In [ ]:
tag_set_10000=make_brandset(good_tag_lines[0:10000])
tag_dict_10000=make_dict(tag_set_10000)
brand_set_10000=make_brandset(Coordinate_lines[0:10000])
brand_dict_10000=make_dict(brand_set_10000)